<a href="https://colab.research.google.com/github/Suhail-46/Shopper-Spectrum-Segmentation-and-Recommendations/blob/main/Shopper_Spectrum_Segmentation_and_Recommendations.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
# Pushing the .csv file into data frame as 'df'
import pandas as pd
df = pd.read_csv("/content/online_retail.csv")

In [ ]:
# View of converted data frame
df

InvoiceNo StockCode                          Description  Quantity  \
0         536365    85123A   WHITE HANGING HEART T-LIGHT HOLDER         6   
1         536365     71053                  WHITE METAL LANTERN         6   
2         536365    84406B       CREAM CUPID HEARTS COAT HANGER         8   
3         536365    84029G  KNITTED UNION FLAG HOT WATER BOTTLE         6   
4         536365    84029E       RED WOOLLY HOTTIE WHITE HEART.         6   
...          ...       ...                                  ...       ...   
541904    581587     22613          PACK OF 20 SPACEBOY NAPKINS        12   
541905    581587     22899         CHILDREN'S APRON DOLLY GIRL          6   
541906    581587     23254        CHILDRENS CUTLERY DOLLY GIRL          4   
541907    581587     23255      CHILDRENS CUTLERY CIRCUS PARADE         4   
541908    581587     22138        BAKING SET 9 PIECE RETROSPOT          3   

                InvoiceDate  UnitPrice  CustomerID         Country  
0       2022-12-01 08:26:00       2.55     17850.0  United Kingdom  
1       2022-12-01 08:26:00       3.39     17850.0  United Kingdom  
2       2022-12-01 08:26:00       2.75     17850.0  United Kingdom  
3       2022-12-01 08:26:00       3.39     17850.0  United Kingdom  
4       2022-12-01 08:26:00       3.39     17850.0  United Kingdom  
...                     ...        ...         ...             ...  
541904  2023-12-09 12:50:00       0.85     12680.0          France  
541905  2023-12-09 12:50:00       2.10     12680.0          France  
541906  2023-12-09 12:50:00       4.15     12680.0          France  
541907  2023-12-09 12:50:00       4.15     12680.0          France  
541908  2023-12-09 12:50:00       4.95     12680.0          France  

[541909 rows x 8 columns]

In [ ]:
# Shape of data frame to check count of rows and column
df.shape

(541909, 8)

In [ ]:
# Wholesome information of data frame printed to know the datatypes, null values, count of row and columns.
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 541909 entries, 0 to 541908
Data columns (total 8 columns):
 #   Column       Non-Null Count   Dtype  
---  ------       --------------   -----  
 0   InvoiceNo    541909 non-null  object 
 1   StockCode    541909 non-null  object 
 2   Description  540455 non-null  object 
 3   Quantity     541909 non-null  int64  
 4   InvoiceDate  541909 non-null  object 
 5   UnitPrice    541909 non-null  float64
 6   CustomerID   406829 non-null  float64
 7   Country      541909 non-null  object 
dtypes: float64(2), int64(1), object(5)
memory usage: 33.1+ MB


In [ ]:
# From below result we can conclude the count of unique values in each column
for i in df.columns:
  print(i,"=",df[i].nunique())

InvoiceNo = 25900
StockCode = 4070
Description = 4223
Quantity = 722
InvoiceDate = 23260
UnitPrice = 1630
CustomerID = 4372
Country = 38


The Country column is having only 38 unique countries which can be framed as categorical column and remaining are continuous columns

In [ ]:
# Checking for spelling mistakes in Country column
df['Country'].unique()

array(['United Kingdom', 'France', 'Australia', 'Netherlands', 'Germany',
       'Norway', 'EIRE', 'Switzerland', 'Spain', 'Poland', 'Portugal',
       'Italy', 'Belgium', 'Lithuania', 'Japan', 'Iceland',
       'Channel Islands', 'Denmark', 'Cyprus', 'Sweden', 'Austria',
       'Israel', 'Finland', 'Bahrain', 'Greece', 'Hong Kong', 'Singapore',
       'Lebanon', 'United Arab Emirates', 'Saudi Arabia',
       'Czech Republic', 'Canada', 'Unspecified', 'Brazil', 'USA',
       'European Community', 'Malta', 'RSA'], dtype=object)

In [ ]:
# Checking for duplicates in data frame
df.duplicated().sum()

np.int64(5268)

In [ ]:
# There are around 5268 rows of data is duplicated and it will not give any mean for model so removing them
df.drop_duplicates(keep = "first",inplace = True) # first occurence is considered as original

In [ ]:
# Checking for null values in data frame
df.isnull().sum()

InvoiceNo           0
StockCode           0
Description      1454
Quantity            0
InvoiceDate         0
UnitPrice           0
CustomerID     135037
Country             0
dtype: int64

From the entire dataset, there are only 1,454 null values in the Description column (0.27%), so removing them will have no significant impact on machine learning.

In [ ]:
# Dropped the record which has null values in Description column
df.dropna(subset=['Description'],inplace = True)
df['Description'].isna().sum()

np.int64(0)

In [ ]:
# Removed null values from CustomerID as per client requirement
df.dropna(subset=['CustomerID'],inplace = True)
df['CustomerID'].isna().sum()

np.int64(0)

In [ ]:
# Validation performed to ensure that all null values in the DataFrame have been handled.
df.isnull().sum()

InvoiceNo      0
StockCode      0
Description    0
Quantity       0
InvoiceDate    0
UnitPrice      0
CustomerID     0
Country        0
dtype: int64

In [ ]:
# Extracted cancelled invoices from the dataset using the InvoiceNo column.
cancel_invoice = df["InvoiceNo"].astype(str).str.startswith('C')
df[cancel_invoice].shape

(8872, 8)

In [ ]:
# Removed cancelled invoices from InvoiceNo as per client requirement
df = df[~cancel_invoice]

In [ ]:
# Removed rows with negative Quantity and rows with zero or negative UnitPrice as per client requirement.
df = df[(df['Quantity'] > 0) & (df['UnitPrice'] > 0)]

In [ ]:
# Next step of data processing is to convert data types into numeric so written the below code to identify non-numeric columns.
for i in df.select_dtypes(include=["object"]).columns:
  print(i)

InvoiceNo
StockCode
Description
InvoiceDate
Country


From the result of the unique counts of the columns listed below, it was concluded that these columns have relatively few distinct values compared to the large dataset. Hence, they fall under categorical columns

*   InvoiceNo
*   StockCode
*   Description
*   InvoiceDate
*   CustomerID
*   Country




In [ ]:
# Converted InvoiceDate column from object to datetime
df["InvoiceDate"]=pd.to_datetime(df["InvoiceDate"])

In [ ]:
# Extracted datetime components for pattern analysis in ML
df['Year'] = df['InvoiceDate'].dt.year
df['Month'] = df['InvoiceDate'].dt.month
df['Day'] = df['InvoiceDate'].dt.day
df['Hour'] = df['InvoiceDate'].dt.hour
df['Minute'] = df['InvoiceDate'].dt.minute
df['Second'] = df['InvoiceDate'].dt.second
df['Weekday'] = df['InvoiceDate'].dt.weekday
df['Week'] = df['InvoiceDate'].dt.isocalendar().week

In [ ]:
# Dropped InvoiceDate column after extracting all datetime components
df.drop("InvoiceDate", axis=1, inplace = True)

From the above execution, only InvoiceDate was suitable for conversion and extraction. Since the other columns are not in numerical form, it was concluded that all non-numerical columns should be encoded as part of data preprocessing.

In [ ]:
# Checked the columns suitable for encoding.
for i in df.select_dtypes(include=["object"]).columns:
  print(i)

InvoiceNo
StockCode
Description
Country


In [ ]:
# Converted InvoiceNo and CustomerID columns to float since they are already numeric
df['InvoiceNo'] = df['InvoiceNo'].astype(float)
df['CustomerID'] = df['CustomerID'].astype(float)

In [ ]:
# Encoding all the categorized column into Numerical column using Label encoder
from sklearn.preprocessing import LabelEncoder
encode = LabelEncoder()
df["Description"] = encode.fit_transform(df[["Description"]])
df["Country"] = encode.fit_transform(df[["Country"]])
df["StockCode"] = encode.fit_transform(df[["StockCode"]])

/usr/local/lib/python3.12/dist-packages/sklearn/preprocessing/_label.py:110: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/usr/local/lib/python3.12/dist-packages/sklearn/preprocessing/_label.py:110: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/usr/local/lib/python3.12/dist-packages/sklearn/preprocessing/_label.py:110: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


In [ ]:
# Validated the created columns and encoded values by printing the first 5 record using head function
df.head()

InvoiceNo  StockCode  Description  Quantity  UnitPrice  CustomerID  \
0   536365.0       3233         3698         6       2.55     17850.0   
1   536365.0       2643         3706         6       3.39     17850.0   
2   536365.0       2847          858         8       2.75     17850.0   
3   536365.0       2795         1804         6       3.39     17850.0   
4   536365.0       2794         2763         6       3.39     17850.0   

   Country  Year  Month  Day  Hour  Minute  Second  Weekday  Week  
0       35  2022     12    1     8      26       0        3    48  
1       35  2022     12    1     8      26       0        3    48  
2       35  2022     12    1     8      26       0        3    48  
3       35  2022     12    1     8      26       0        3    48  
4       35  2022     12    1     8      26       0        3    48

In [ ]:
# Exploratory Data Analysis (EDA) using visualizations
import plotly.express as px
import matplotlib.pyplot as plt
import seaborn as sns

In [ ]:
# Transaction volume(InvoiceNo) vs. Country: Examine how transactions vary with country.
fig = px.scatter(
    df,
    x='Country',
    y='InvoiceNo',
    title='InvoiceNo vs. Country',
    labels={'InvoiceNo': 'Transactions', 'Country': 'Countries'},
    opacity=0.5  # makes overlapping points more visible
)

fig.show()

In [ ]:
df.shape

(392692, 15)

In [ ]:
df.head()